In [53]:
%load_ext autoreload
%autoreload 2
%matplotlib inline  

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.offline as pl
pl.init_notebook_mode(connected=True)
import plotly.graph_objs as go

from datetime import datetime, timedelta
import parseIntervalFiles as pif
import parseActivityFiles as paf
#pun intended :)
import consolidateFiles as cf
import datacleaning as cl
import dataviz as dv

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
verbose = True

PATH = "C:\\Users\\ju\\GDrive\\Projects\\HeRV\\Data\\"
RAW = PATH + "Raw"

In [3]:
file = PATH + "PreProcessed\\sessions.xlsx"
df = pd.read_excel(file)
df.sample(5)

activity  beatscount  duration           hf       hfnu  \
219   focused-active        1618      1279   316.352672  26.025679   
123   focused-active        2576      1907   709.563556  47.059847   
204            sleep       36209     29727  2593.709765  62.863897   
342   focused-active        1260       840   159.534850  12.167461   
294  focused-passive        1125       780   582.732962  34.497499   

              lf     lf_hf       lfnu        mhr        mrri   ...     \
219   899.187847  2.842359  73.974321  75.131677  802.743511   ...      
123   798.226217  1.124954  52.940153  79.922443  757.351320   ...      
204  1532.203341  0.590738  37.136103  73.273900  834.775084   ...      
342  1151.624926  7.218642  87.832539  88.810482  682.342857   ...      
294  1106.470553  1.898761  65.502501  89.111180  686.403556   ...      

     posture removed_artifacts      rmssd        sdnn               start  \
219      sit                 4  39.155542   55.053482 2017-10-30 00:00:01   
123      sit                 4  50.918332   67.459799 2017-11-07 14:47:31   
204      lie                 1  73.981658  118.897841 2018-04-19 01:44:04   
342    stand                 0  21.658480   68.844819 2017-10-11 12:11:00   
294      sit                 8  64.029526   99.171357 2017-10-05 09:32:00   

                   stop  total_power user          vlf  sess_id  
219 2017-10-30 00:21:20  1743.593669    1   528.053150      219  
123 2017-11-07 15:19:18  2379.311469    0   871.521695      123  
204 2018-04-19 09:59:31  5597.172747    0  1471.259641      204  
342 2017-10-11 12:25:00  2432.265040    2  1121.105264      342  
294 2017-10-05 09:45:00  2639.250081    2   950.046566      294  

[5 rows x 23 columns]

In [4]:
len(df)

447

## Plotting random examples of RR time series for each type of activity

In [5]:
for act in df['activity'].unique():
    v = df[df['activity'] == act].sample(1)
    print('---------------- ', act, ' ---------------')
    for i in range(1):
        print('USER: ', v.iloc[i]['user'])
        dv.plot_sess_rr(v.iloc[i], RAW, act)

----------------  focused-active  ---------------
USER:  1


----------------  leisure-active  ---------------
USER:  0


----------------  eat  ---------------
USER:  0


----------------  movement  ---------------
USER:  0


----------------  leisure-passive  ---------------
USER:  1


...

----------------  rest-passive  ---------------
USER:  0


----------------  rest-active  ---------------
USER:  0


----------------  household-chores  ---------------
USER:  0


----------------  focused-passive  ---------------
USER:  2


----------------  exercise  ---------------
USER:  3


## Plotting features summary for each type of session
---

In [6]:
dfc = df[df['hf'] < 7000]
print(len(df) - len(dfc))
print(len(dfc))

40
407


In [8]:
dfc = dfc[dfc['lf'] < 7000]
print(len(dfc))

406


In [25]:
for user in range(3):    
    dfu = dfc[dfc['user'] == user]
    print('---------------------------------------- ', user, ' ----------------------------------------')
    for feat in cl.features_all:
        dv.boxplot_compare(dfu, feat, groupby='activity', min_examples=2)

----------------------------------------  0  ----------------------------------------


----------------------------------------  1  ----------------------------------------


----------------------------------------  2  ----------------------------------------


## Assessing how features evolve within a session
---

### Load sessions fragmented in 60 seconds

In [138]:
fdf = pd.read_excel('../data/fragments/df_060_30.xlsx')

In [139]:
fdf.describe()

beatcount            hf          hfnu            lf         lf_hf  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      80.363334   1773.941653     49.715246   1531.153352      2.214625   
std       20.802385   2950.548394     25.388744   2840.047921      3.537051   
min       37.000000      0.077152      0.749662      0.173046      0.005172   
25%       68.000000    225.169651     27.548188    217.729426      0.399618   
50%       77.000000    580.018943     49.822851    596.142299      1.007111   
75%       87.000000   1604.705984     71.448061   1579.597222      2.630003   
max      186.000000  14976.717492     99.485487  38797.808704    132.393456   

               lfnu           mhr          mrri          nn50         order  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      50.284754     80.330579    793.353147     15.412052     90.554724   
std       25.388744     19.158152    168.537135     13.509879    113.640431   
min        0.514513     43.512674    327.907104      0.000000      0.000000   
25%       28.551939     68.751270    694.717647      4.000000     12.000000   
50%       50.177149     77.087860    785.960526     12.000000     36.000000   
75%       72.451812     87.477389    882.623188     24.000000    132.000000   
max       99.250338    183.052548   1382.954545    100.000000    571.000000   

              pnn50         rmssd          sdnn          sess   total_power  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      22.114158     61.525357     70.406003    213.207768   4763.583921   
std       20.560198     52.131322     45.708567    137.217487   6895.635161   
min        0.000000      1.424952      2.100095      0.000000      0.980344   
25%        4.878049     26.782073     38.349954     97.000000    962.270918   
50%       16.438356     42.529168     56.484266    188.000000   2101.509697   
75%       34.375000     79.151921     89.612703    349.000000   5157.723253   
max       94.444444    431.483256    328.385002    446.000000  70185.639553   

               user           vlf  
count  19233.000000  19233.000000  
mean       1.298393   1458.488916  
std        1.902666   3183.156723  
min        0.000000      0.000000  
25%        0.000000    180.706275  
50%        0.000000    514.230086  
75%        2.000000   1428.327446  
max        6.000000  61682.589010

### Helper to choose an activity

In [205]:
df.loc[(df['activity']=='movement') & (df['user']== 0)][['user', 'activity', 'start', 'duration', 'beatscount']].sort_values(by='duration', ascending=False)

user  activity               start  duration  beatscount
50      0  movement 2017-10-12 10:24:22     11144       14222
55      0  movement 2017-10-12 19:45:58      8176       14381
85      0  movement 2017-10-15 14:46:02      4893        6385
75      0  movement 2017-10-14 15:38:20      3100        5415
192     0  movement 2018-02-21 14:24:12      2881        5967
113     0  movement 2017-11-03 08:21:33      2847        5292
180     0  movement 2018-02-01 21:11:15      2790        4875
59      0  movement 2017-10-13 10:40:00      2579        4863
97      0  movement 2017-10-29 08:40:11      2421        5008
205     0  movement 2018-04-19 10:30:47      2375        4989
69      0  movement 2017-10-14 11:10:36      2267        4230
131     0  movement 2017-11-07 21:31:08      2241        3680
197     0  movement 2018-04-15 18:52:17      2135        4498
198     0  movement 2018-04-16 11:31:17      2102        3950
147     0  movement 2017-11-18 10:37:28      2023        4134
167     0  movement 2017-12-13 15:03:03      1962        1841
195     0  movement 2018-03-14 07:31:13      1869        3332
41      0  movement 2017-10-10 20:50:06      1794        2750
53      0  movement 2017-10-12 18:54:27      1650        2511
186     0  movement 2018-02-08 11:13:16      1536        3054
152     0  movement 2017-11-22 19:37:39      1355        2374
139     0  movement 2017-11-09 16:28:26      1352        2551
7       0  movement 2017-09-30 09:50:00      1200        2039
190     0  movement 2018-02-20 18:49:20      1184        2153
141     0  movement 2017-11-15 11:53:37      1139        1946
26      0  movement 2017-10-04 15:14:23      1134        2336
40      0  movement 2017-10-10 20:32:23      1062        1764
173     0  movement 2018-01-23 17:44:09       994        1868
171     0  movement 2018-01-12 17:53:04       971        2066
109     0  movement 2017-11-01 11:29:55       953        2243
4       0  movement 2017-09-29 19:14:15       275         276
57      0  movement 2017-10-12 22:40:54       250         440
177     0  movement 2018-01-31 17:08:51       240         412

### Exercise
20 min switch exercise type (aerobic -> strength)

In [190]:
pp = fdf.loc[fdf['sess'] == 207].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### Movement

In [209]:
pp = fdf.loc[fdf['sess'] == 198].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### Sleeping

In [176]:
pp = fdf.loc[fdf['sess'] == 188].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=5))

### A long session of lectures

In [197]:
pp = fdf.loc[fdf['sess'] == 31].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### A single lecture
148 - lose focus after an hour <br>
107 - keep focus

In [204]:
pp = fdf.loc[fdf['sess'] == 107].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### Work session
seems like a pomodoro break there :)

In [185]:
pp = fdf.loc[fdf['sess'] == 230].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))